In [1]:
import re
import pandas as pd
import numpy as np
from tqdm import tqdm
from sklearn.feature_extraction.text import CountVectorizer
from konlpy.tag import Mecab
from bertopic import BERTopic
import matplotlib.pylab as plt
from bertopic.representation import MaximalMarginalRelevance
from umap import UMAP
from hdbscan import HDBSCAN
from bertopic.vectorizers import ClassTfidfTransformer

import pandas as pd
import glob
import os
import re  
import numpy as np
from datetime import datetime
import dateutil.parser as parser  


df=pd.read_csv('massmedia2018_2023.csv', parse_dates=['date']) 
#df=pd.read_csv('massmedia2009_2023.csv', parse_dates=['date']) 
#df=pd.read_csv('massmedia2009_2017.csv', parse_dates=['date']) 
#df=pd.read_csv('massmedia2022_2023.csv', parse_dates=['date']) 

#df=df.dropna()

timestamps = df['date'].tolist()

In [2]:
df['texts'] = df['texts'].astype(str)
df.head(5)

Unnamed: 0.6  Unnamed: 0.5  Unnamed: 0.4  Unnamed: 0.3  Unnamed: 0  \
0          3183          3183        1238.0           NaN        3758   
1          3184          3184        1239.0           NaN        1972   
2          3185          3185        1240.0           NaN        7104   
3          3186          3186        1242.0           NaN        6748   
4          3187          3187        3186.0        1241.0        6743   

                 date                                               link  \
0 2018-01-01 03:00:00  https://www.donga.com/news/article/all/2018010...   
1 2018-01-02 01:00:00        https://www.joongang.co.kr/article/22250544   
2 2018-01-03 14:21:00        https://www.joongang.co.kr/article/22255512   
3 2018-01-03 17:30:00        https://www.joongang.co.kr/article/22256536   
4 2018-01-03 17:30:00        https://www.joongang.co.kr/article/22256536   

                                           news text  Unnamed: 0.1 title  \
0  \n최유안\n일러스트레이션 김수진 기자 soojin@donga.com1. 인터뷰 \...        3758.0   NaN   
1  \n  “혁신도시의 완성을 위해서는 제주가 잘할 수 있는 농업·관광 분야와의 융·복...        1972.0   NaN   
2  \n여권에서 남북관계 해빙에 대한 기대감이 커지고 있다.   북한 김정은 노동당 위...        7104.0   NaN   
3  \n  혐오 발언이나 가짜 뉴스를 방치하는 소셜미디어 기업에 최고 5000만 유로(...        6748.0   NaN   
4  \n  혐오 발언이나 가짜 뉴스를 방치하는 소셜미디어 기업에 최고 5000만 유로(...        6743.0   NaN   

  article text                                               text  \
0          NaN  \n최유안\n일러스트레이션 김수진 기자 soojin@donga.com1. 인터뷰 \...   
1          NaN  \n  “혁신도시의 완성을 위해서는 제주가 잘할 수 있는 농업·관광 분야와의 융·복...   
2          NaN  \n여권에서 남북관계 해빙에 대한 기대감이 커지고 있다.   북한 김정은 노동당 위...   
3          NaN  \n  혐오 발언이나 가짜 뉴스를 방치하는 소셜미디어 기업에 최고 5000만 유로(...   
4          NaN  \n  혐오 발언이나 가짜 뉴스를 방치하는 소셜미디어 기업에 최고 5000만 유로(...   

                                               texts  Unnamed: 0.2  
0  최유안 일러스트레이션 김수진 기자 . . 인터뷰 장맛비가 오는 저녁 나는 학위 논문...           NaN  
1  “혁신도시의 완성을 위해서는 제주가 잘할 있는 농업·관광 분야와의 융·복합 특화가 ...           NaN  
2  여권에서 남북관계 해빙에 대한 기대감이 커지고 있다. 북한 김정은 노동당 위원장이 ...           NaN  
3  혐오 발언이나 가짜 뉴스를 방치하는 소셜미디어 기업에 최고 유로 약 억원 벌금을 물...           NaN  
4  혐오 발언이나 가짜 뉴스를 방치하는 소셜미디어 기업에 최고 유로 약 억원 벌금을 물...           NaN

In [3]:
documents = df['texts'].astype(str)


documents = [line.strip() for line in df.texts]
preprocessed_documents = []

for line in tqdm(documents):
  if line and not line.replace(' ', '').isdecimal():
    preprocessed_documents.append(line)

text=''.join(preprocessed_documents[:10000])
text=text.split('.')


class CustomTokenizer:
    def __init__(self, tagger):
        self.tagger = tagger
    def __call__(self, sent):
        sent = sent[:1000000]
        word_tokens = self.tagger.nouns(sent) #word_tokens = self.tagger.morphs(sent)
        result = [word for word in word_tokens if len(word) > 1]
        return result
    
seed_topic_list = [['실업', '일자리', '작업 경쟁','취업 경쟁','직장 잃','경쟁'], #1. Common Arguments against Immigration: “immigrants take jobs, lower wages, hurt the poor” (ref: https://www.cato.org/blog/14-most-common-arguments-against-immigration-why-theyre-wrong)
                   ['건강 보험', '병원', '복지','보건의료사비스', '보건의료', '보건의료요구','의료 혜택',  '보험 혜택',  '의료', '건강', '의료혜택','보건의료정책','IHS', 'NHS','의료 서비스', '사회복지'], #2. Common Arguments against Immigration : “ abuse welfare”
                   ['세금','불경기'], #3. Common Arguments against Immigration: “increase budget deficit and government debt”
                   ['한국어 실력', '문화 교류','통합','언어장벽', '동화','사회통합 프로그램','공동'], #4.Common Arguments against Immigration: “ don’t assimilate, integrate”community
                   ['불법','범죄','위험', '살인', '강도', '절도', '매춘', '마약', '사이버 범죄', '텔레뱅킹 사기', '피싱', '외국인 범죄', '위조범', '밀수품', '산업연수생 범죄'], #5. Common Arguments against Immigration: “source of crime”
                   ['테러','테러분자','테러리즘','테러리스트','사보타주'], #6.Common Arguments against Immigration: “terrorism” 
                   ['민족주의','한국적 가치관, 한국성','국가 이미지','한국 이미지'], #7.Common Arguments against Immigration: national sovereignty 
                   ['정부','법무부','윤석열','문재인','박근혜','이명박','노무현','김대중','대통령','통치'], #8.ruling class - government
                   ['국적','교포', '미국', '일본', '이집트',  '주전자','고려인', '러시아','흑인','아랍','라틴아메리카 ' , '베트남', '둥포', '백인', '조선족', '러시아인', '미국인', '유럽인', '서구인','서양인', '동남아시아인', '동남아인', '우즈벡인', '우즈베키스탄 이주', '중국인', '중국', '아프리카', '인도', '우크라이나',  '중동', '몽골인', '몽골', '탈북이주민', '북한이탈주민'], #9.dividing the working class with identity politics:racism and ethnicity 인종
                   ['이주여성','여성이주노동자','여성','여자', '젠더'], #10.dividing the working class with identity politics: gender discrimination 성별
                   ['MTU', '조합', '이주노동희망센터', '이민자 센터', '연대', '이주노동자노동조합', '이주노조', '이주노동자 노동조합', '이주민센터 친구','상담'], #11.uniting the working class with union
                   ['국제결혼', '외국인 신부', '결혼이민자', '결혼이민','결혼이주자', '결혼 중개업', '이민자 부모','결혼', '이혼', '아내', '남편', '신부', '가정 폭력', '가족 폭력'], #12.dividing migrants by migrant status and place in the online migration debate: marriage
                   ['가족','다문화주의','외국인 아동','다문화 가정','이민자 부모', '임산부','임신','어린이', '부모님','다문화가족'], #13.Family
                   ['무슬림','이슬람교도','이슬람','무슬리마'], #14. divide by religion
                   ['선생님','영어 선생님', '부자', '사업가','투자자','교수','상용 비자'], #15.status: high payed worker
                   ['농장','건설','선박', '어업','E9', '고용허가제', '서비스업', '농축산업', '건설업','제조업','건설공사', '작물재배업','축산업','양식어업','소금채취업', ' 비전문취업','건설폐기물 처리업','육체노동','공장', '건설노동자', '계절 노동자', '3D 업종','산업연수생 시스템'], #16.status: low payed workers in 3d industries
                   ['가사도우미', '입주도우미', '육아도우미' , '간병도우미', '베이비시터', '외국인 가사도우미', '돌봄도우미', '간병인', '도우미','요식업','식업'], #17.status: gendered work in service industry, nurse, cleaning staff
                   ['관광객', '여행', '문화', '여행자','관광'], #18.status: tourist
                   ['학생', '학교', '대학교', '대학생', '교환 학생','유학비자', '유학', '어학연수', '교환학생', '연구유학'], #19.status: student
                   ['탈북자','북한이탈주민','탈북','탈북자','탈북민','새터민','북한이탈주민'], #20.north korea refugees
                   ['불법체류자','불법체류 외국인', '불법체류', '미등록', '미등록 이주자', '불쳬자','미등록외국인근로자', '외국인 불법 근로자','무허가 노동자'], #21.status: undocumented immigration
                   ['예멘', '미얀마','파키스탄','방글라데시','에티오피아'], #22.status: refugee based on nationality
                   ['변호사', '법원','비자', '법', '이민법','시민권', '노동법','국적법', '이민 정책', '근로기준법'], #23.immigration law
                   ['출입국관리소', '비자연장', '비자유형변경', '비자신청', '영주권', '체류허가', '비자'], #24.administration
                   ['저임금 노동', '값싼 노동자', '저임금', '최저임금','고용','계급','자본'], #25.wages and work, working class in capitalism
                   ['노동 착취','남용', '착취', '사고', '직장 괴롭힘', '괴롭힘', '근로환경', '작업 조건','폭력','노예'], #26.human rights abuse
                   ['노동시간', '복지', '시설', '산업재해', '임금체불', '시간외 수당', '해고','부상 보상'], #27.working conditions
                   ['경찰단속', '단속','합동단속', '정부합동단속', '단속추방','추방','강제추방','외국인보호소','경찰', '감옥','국경검사','한국경찰','구속'], #28.police state, border, deportation, expulsion
                   ['차별','차별금지','외국인 혐오','소수자',' 배제','불평등','계층','고정관념','낙인','선입견','인종차별','기본권', '평등', '불평등', '편견','인권'], #29.discrimination awareness 
                   ['경제', '경제이주', '경제적 이득', '노동수요','노동력 부족','이윤'], #30.economy    
                   ['비자','신청','발급'], #visa administration (added topic)
                   ['관광','여행'], #(added topic)
                   ['뉴스'], #(added topic)
                   ['망명 신청자','난민','피난자'], #refugees
                   ['친구'], #(added topic)
                   ['자발'], #(added topic)
                   ['종목'], #(added topic)
                   ['영어','한국어'], #(added topic)
                   ['외국인','외국'], #(added topic)
                   ['한국','한국인'], #(added topic)
                   ['일본','일본어'], #(added topic)
                   ['이주노','동자'], #(added topic)
                   #['결혼','여성'], #(added topic)
                   #['결혼','가족'], #(added topic)
                   #['외국인'], #(added topic)
                   #['이민자'], #(added topic)
                   ['결혼','여성','가족'], #(added topic)
                   ['개인','사람','나라','카드','생각']] #(added topic)

    
custom_tokenizer = CustomTokenizer(Mecab())
vectorizer = CountVectorizer(tokenizer=custom_tokenizer, max_features=3000)


umap_model = UMAP(n_neighbors=30, n_components=8, min_dist=0.0, metric='cosine') 


model = BERTopic(embedding_model="sentence-transformers/xlm-r-100langs-bert-base-nli-stsb-mean-tokens", \
                 vectorizer_model=vectorizer,
                 umap_model=umap_model,            
                 seed_topic_list=seed_topic_list,
                 #min_topic_size=35,
                 nr_topics=31,
                 top_n_words=20,
                 calculate_probabilities=True)




topics, probs = model.fit_transform(documents) # Train your BERTopic model

model.save('massmedia2018_2023.h5')

for i in range(0, 33): 
  print(i,'번째 토픽 :', model.get_topic(i))


similar_topics, similarity = \
model.find_topics("여성", top_n = 10) 

print("Most Similar Topic Info: \n{}".format(model.get_topic(similar_topics[0])))
print("Similarity Score: {}".format(similarity[0]))

print("\n Most Similar Topic Info: \n{}".format(model.get_topic(similar_topics[1])))
print("Similarity Score: {}".format(similarity[1]))

print("\n Most Similar Topic Info: \n{}".format(model.get_topic(similar_topics[2])))
print("Similarity Score: {}".format(similarity[2]))

100%|██████████| 10939/10939 [00:00<00:00, 36219.42it/s]
OMP: Info #276: omp_set_nested routine deprecated, please use omp_set_max_active_levels instead.
/home/cla/miniconda3/envs/env_full2/lib/python3.9/site-packages/scipy/sparse/_index.py:146: SparseEfficiencyWarning: Changing the sparsity structure of a csr_matrix is expensive. lil_matrix is more efficient.
  self._set_arrayXarray(i, j, x)


0 번째 토픽 : [('한국', 0.022230796860061575), ('난민', 0.021245177313063492), ('베트남', 0.018176622364288117), ('경찰', 0.01740647313009728), ('여성', 0.0168946436197601), ('결혼', 0.013813023439212667), ('정부', 0.01381117689488733), ('사람', 0.012294487385114117), ('서울', 0.012213293749707142), ('한국인', 0.012128458015847417), ('신청', 0.011630819744823289), ('문화', 0.01156828424419099), ('대표', 0.011223159889391321), ('일본', 0.011119434065685581), ('문제', 0.010426986995967917), ('지역', 0.010365804869886731), ('아이', 0.010206153418180595), ('가족', 0.010088617570545225), ('국회', 0.009978299506809101), ('합정', 0.009918739251137168)]
1 번째 토픽 : [('외국인', 0.03844221550308196), ('근로자', 0.035820236126298186), ('계절', 0.02471803664348757), ('시장', 0.02232268962484189), ('인력', 0.017568798636321915), ('중국', 0.015317994824586534), ('지수', 0.015069282669442418), ('상승', 0.014959787221148966), ('고용', 0.01440221299120553), ('금리', 0.01415371933606837), ('코로나', 0.014043223394655234), ('대출', 0.013784852666670159), ('농가', 0.01365836187923

In [4]:
fig = model.visualize_barchart()
fig.write_html("massmedia2018_2023junenewsbarchart.html")
fig.show()


fig = model.visualize_topics()
fig.write_html("massmedia2018_2023junenewstopics.html")
fig.show()


fig = model.visualize_hierarchy()
fig.write_html("massmedia2018_2023junenewshierarchy.html")
fig.show()


fig = model.visualize_heatmap()
fig.write_html("massmedia2018_2023junenewsheatmap.html")
fig.show()


fig = model.visualize_term_rank()
fig.write_html("massmedia2018_2023junenewstermrank.html")
fig.show()


fig = model.visualize_term_rank(log_scale=True)
fig.write_html("massmedia2018_2023junenewslogtermrank.html")
fig.show()

#junemassmedia2018_2023news

In [5]:
topics_over_time = model.topics_over_time(documents, timestamps)
fig = model.visualize_topics_over_time(topics_over_time)
fig.write_html("massmedia2018_2023junenewstopicstime.html")
fig.show()

In [6]:
model.get_topic_info()

Topic  Count                   Name
0      -1   3181         -1_난민_경찰_여성_중국
1       0   5644         0_한국_난민_베트남_경찰
2       1    442        1_외국인_근로자_계절_시장
3       2    345     2_러시아_우크라_우크라이나_전쟁
4       3    170       3_트럼프_대통령_민주당_미국
5       4    138         4_독일_메르켈_총리_노예
6       5    119         5_이민_정책_인구_이민정
7       6    117         6_중국_대만_외교_중국인
8       7    112        7_월드컵_카타르_경기_축구
9       8     89  8_아프간_탈레반_아프가니스탄_파키스탄
10      9     82          9_차별_인권_혐오_권고
11     10     45         10_문화_교육_아이_학교
12     11     44       11_영화_감독_영화제_변호사
13     12     44    12_마을버스_버스_교통사고_보행자
14     13     38    13_이스라엘_아랍_팔레스타인_중동
15     14     36    14_필리핀_중국_차이나타운_중국인
16     15     36       15_이라크_교회_하나님_교황
17     16     29         16_마약_태국_대마_주점
18     17     28       17_올림픽_베이징_여자_난민
19     18     23      18_여성_성매매_업주_로하우스
20     19     22        19_공간_김수근_건축_해녀
21     20     20      20_터키_시리아_쿠르드족_난민
22     21     20         21_화성_탐사_지구_로버
23     22     18       22_스위스_자살_조력_러시아
24     23     18    23_뉴욕_지은이_히스패닉_브루클린
25     24     17       24_연금_개혁_스웨덴_리스터
26     25     14      25_프랑스_쿠르드족_파리_여성
27     26     13        26_홍콩_시위_중국_본토인
28     27     12         27_토론_여권_한국_영어
29     28     12       28_리비아_이주자_이상_사막
30     29     11       29_애란원_미혼모_엄마_임신

In [7]:
model.get_topics()

{-1: [('난민', 0.020751170074977846),
  ('경찰', 0.01514254448659657),
  ('여성', 0.014763088454583462),
  ('중국', 0.01393823366797438),
  ('한국', 0.013882133868415516),
  ('정부', 0.012158217399546116),
  ('미국', 0.011261171582219336),
  ('사람', 0.011235391541773746),
  ('외국인', 0.011003217863741237),
  ('지역', 0.010585010166235958),
  ('북한', 0.010514810187574237),
  ('제주', 0.01046200905286162),
  ('유럽', 0.010354183145160603),
  ('대학', 0.009330006432307324),
  ('세계', 0.00927048512418314),
  ('불법체류', 0.009127483447422823),
  ('기자', 0.008998555520950548),
  ('서울', 0.008866210312807822),
  ('국가', 0.008662832242223384),
  ('지난해', 0.008554059994751525)],
 0: [('한국', 0.022230796860061575),
  ('난민', 0.021245177313063492),
  ('베트남', 0.018176622364288117),
  ('경찰', 0.01740647313009728),
  ('여성', 0.0168946436197601),
  ('결혼', 0.013813023439212667),
  ('정부', 0.01381117689488733),
  ('사람', 0.012294487385114117),
  ('서울', 0.012213293749707142),
  ('한국인', 0.012128458015847417),
  ('신청', 0.011630819744823289),
  

In [8]:
model.get_representative_docs()

{-1: ['관광객이 많아져서 일을 구했어요. 지난달 기자와 만난 예멘 난민 a씨 환하게 웃었다. 그는 최근 제주 시내 치킨집에서 일자리를 얻었다고 한다. 제주도로 들어오는 국내 관광객들이 점차 늘어난 덕을 봤다. 그는 코로나 팬더믹 초기에는 손님이 없어 원래 일하던 곳에서도 잘리고 새로운 일자리를 구하지 못해 전전긍긍했었다 고 전했다. <‘혐오 팬더믹’ 한국을 삼키다> 회 제노포비아 대안 멀지 않은 곳에 a씨의 구직을 도와준 건 천주교제주교구 나오미센터 연우 활동명· 씨다. 연우씨 역시 살 시리아에서 제주도로 건너와 난민 지위를 인정받고 이곳에 정착했다. 그는 전과 상황이 다르다. 요즘은 난민이라고 고용된다 면서 성실하게 일하는 걸 주민들도 알기 때문 이라고 덧붙였다. 코로나 발 發 위기에 제노포비아 외국인 혐오 전 세계서 확산하고 있다. 인종차별 경제난 등과 겹친 제노포비아는 쉽게 가라앉지 않을 전망이다. 정작 예멘 난민 이주 문제로 홍역을 치렀던 제주도는 조용하다. 전 예방 주사를 맞았기 때문일까. 중앙일보 특별취재팀은 제주 현지 취재를 바탕으로 난민 혐오의 근거와 대안을 따져봤다. 한국에서 외국인 혐오하면 주로 중국인·중국 동포나 일본인 이웃 국가를 떠올린다. 특징이 더 있다. 동남아시아 아프리카 가난한 국가 출신을 혐오하는 이른바 gdp 차별주의 다. 외국인들은 gdp 순서대로 서열화된다. 영미권 백인들은 우리나라 사람들의 호의를 받으며 산다. 정책적으로 비자도 쉽게 취득하며 체류 기간도 길다. 영주권 취득도 쉽고 직업 선택과 직장 이전의 자유도 누린다. 이주 노동자들은 대우를 받지 못한다. 박민영 작가 책 『지금 혐오하셨네요』 중 여름 내전을 피하려는 예멘 난민 명이 제주도에 발을 디뎠을 때도 그랬다. 한국 사회가 보인 반응은 이슬람 혐오와 결합한 gdp 차별주의였다. 예멘 난민 인당 만원의 세금이 지급됐다 대부분은 가짜 난민이다 무임승차론 퍼졌다. 일각에선 난민을 잠재적 테러리스트 간주하며 국가 안보에 위협이 된다고 날을 세웠다. 대부분 사실과 거